# Indoor attenuation using FSPL and partition losses

Data from the exercise:

In [1]:
C = 300e6  # Speed of light in m/s
F = 2e9  # Frequency in Hz

According to the article [How to Measure Wall Attenuation For Spotless Wi-Fi Network Designs](https://www.ekahau.com/blog/how-to-measure-wall-attenuation-for-spotless-wi-fi-network-designs/):

In [2]:
LOSS_GLASS_PARTITION_DB = 2  # dB (1-3)
LOSS_CONCRETE_DB = 12  # dB
WALL_PIECE_VERTICAL = 3  # m
WALL_PIECE_HORIZONTAL = 5  # m

The longest paths are from the top left and right to the base station. On the path we have:

In [3]:
(partition_loss_db := 2 * LOSS_GLASS_PARTITION_DB + LOSS_CONCRETE_DB)

16

The total loss based on:

1. free-space path loss $L_\mathrm{fs}$
2. indoor partition losses

Define $L_\mathrm{fs}$

In [4]:
from sympy import Eq, pi, solve, symbols

l, d, f, c = symbols(r"L_\mathrm{fs} d f c", positive=True)
(eq := Eq(l, (4 * pi * d * f / c) ** 2, evaluate=False))

Eq(L_\mathrm{fs}, 16*pi**2*d**2*f**2/c**2)

Based on the triangle hypotenuse the distance is

In [5]:
from math import sqrt
a = 2 * WALL_PIECE_VERTICAL
b = WALL_PIECE_HORIZONTAL * 1.5
(distance := sqrt(a**2 + b**2))

9.604686356149273

Calculate $L_\mathrm{fs}$

In [6]:
(free_space_loss := eq.rhs.evalf(subs={c: C, f: F, d: distance}))

647446.048711462

in dB

In [14]:
from sympy import log
(free_space_loss_db := (10 * log(free_space_loss)/log(10)).evalf())

58.1120358476393

Total loss:

In [15]:
(total_loss_db := partition_loss_db + free_space_loss_db)

74.1120358476393

---

We used the linear formula above to calculate the loss. We can also use the dB version:

In [9]:
l_db = symbols(r"L_\mathrm{fs[dB]}")
(eq_db := Eq(l_db, (20 * log(d, 10) + 20 * log(f, 10) - 147.55), evaluate=False))

Eq(L_\mathrm{fs[dB]}, 20*log(d)/log(10) + 20*log(f)/log(10) - 147.55)

In [10]:
(free_space_loss_db2 := eq_db.rhs.evalf(subs={f: F, d: distance}))

58.1202636615906

---

## Is there an equivalent free-space distance of a partition loss?

This does not make sense because, for different distances $a$ and $b$, we cannot break the free-space losses down like this $L(a+b) \neq L(a) + L(b)$. This only applies to partition losses.

If you still try to calculate an equivalent distance as follows, the result corresponds to the distance from the transmitter.

In [11]:
(loss_concrete := 10**(LOSS_CONCRETE_DB/20))

3.9810717055349722

Solve for the distance:

In [12]:
(solution := solve(eq, d)[0])

sqrt(L_\mathrm{fs})*c/(4*pi*f)

Evaluate:

In [13]:
distance = solution.evalf(subs={c: C, f: F, l: loss_concrete})
f"{distance:.3f} m"

'0.024 m'

This result only means that the attenuation in the first 24 mm would correspond to a concrete wall. However, this is even a simplification, because radio waves may behave differently in the very proximity of a transmitter.